In [2]:
from threading import Thread, Lock
import random
import operator as _
from time import sleep
from contextlib import contextmanager

class BinaryLock(object):
    def __init__(self):
        self.lock_item_obj = Lock()
        # self.locked = False
        self.x = 0
    
    @contextmanager
    def lock_item(self):
        print("\nlock item called:")
        if self.lock_item_obj.locked():
            print("Wait for locked item")
                # waiting until write_lock released...
            self.lock_item_obj.acquire()
            # while self.lock_item_obj.locked():
            #     print(".",end="")
        else:
            print("Acquire lock_item")
            self.lock_item_obj.acquire()
                
    def lock_release(self):
        print("Release lock")
        if self.lock_item_obj.locked():
            self.lock_item_obj.release()

    @contextmanager
    def locking_item(self):
        try:
            self.lock_item()
            yield
        finally:
            self.lock_release()

    def create_local_variable(self, block):
        variable = 0
        ldic = locals()
        try:
            exec(f"variable = self.{block['variable']}", ldic)
            # print(f"variable {block['variable']} already exists!")
        except AttributeError:
            exec(f"self.{block['variable']} = 0")
            exec(f"variable = self.{block['variable']}", ldic)
            # print(f"variable {block['variable']} created!")
        finally:
            variable = ldic['variable']
        return variable
    # @contextmanager
    # def read_lock(self):
    #     print("\nRead_lock called:")
    #     try :
    #         if not self.write_lock_obj.locked():
    #             print("Acquire read_lock")
    #             self.read_lock_obj = True
    #         else:
    #             print("Wait for write_lock")
    #         yield
    #     finally:
    #         print("Release read_lock")
    #         self.read_lock_obj = False
    
    # @contextmanager
    # def write_lock(self):
    #     print("\nWrite_lock called:")
    #     try :
    #         if not self.read_lock_obj:
    #             print("Acquire write_lock")
    #             self.write_lock_obj.acquire()
    #         else:
    #             print("Wait for read_lock")
    #         yield
    #     finally:
    #         if not self.read_lock_obj:
    #             print("Release write_lock")
    #             self.write_lock_obj.release()
    
    # def read(self):
    #     with self.read_lock():
    #         print("Shared resource value: {}".format(self.x))

    # def write(self, num):
    #     with self.write_lock():
    #         local = self.x
    #         local += num
    #         sleep(3)
    #         self.x = local

# class Concurrency:
#     def __init__(self, locks):
#         self.locks = locks
    
#     def create_transaction(self, transaction, T_num):
#         for block in transaction:
#             print(f"\nT{T_num}, {block['variable']}")
#             operation_name = block['operations'][0]
#             lock_class = self.locks.get(block['variable']) # Fetch variable object from sharedExclusive class.
#             if operation_name == 'read_item':
#                 with lock_class.locking_item():
#                     variable = lock_class.create_local_variable(block)
#                     print(f"{block['variable']}:{variable}")
#                     random_number = random.uniform(0.1,1.5)
#                     print(f"~~ Sleep for {random_number:.2f} s")
#                     sleep(random_number)
                    
#             elif operation_name == 'write_item':
#                 operation_task = block['operations'][1]
#                 with lock_class.locking_item():
#                     variable = lock_class.create_local_variable(block)
#                     print(f"{block['variable']}:{variable}")
#                     operator, operand = operation_task.split()
#                     mapper = {
#                         '+' : _.add,
#                         '-' : _.sub,
#                         '*' : _.mul,
#                         '/' : _.truediv,
#                     }
#                     func = mapper.get(operator, None)
#                     if func:
#                         variable = func(variable, float(operand))
#                     random_number = random.uniform(0.1,1.5)
#                     print(f"~~ Sleep for {random_number:.2f} s")
#                     sleep(random_number)
#                     exec(f"lock_class.{block['variable']} = variable")
    # def locking(self):
    #     with self.lock_item():
    #         print("Shared resource value: {}".format(self.x)) 

In [1]:
a = {}
a['a'] = []
's' not in a.keys()
a['a'] is None
lst = ['a', 'b']
lst.remove('a')
lst

['b']

In [3]:
class Concurrency:
    def __init__(self, locks):
        self.locks = locks
        self.dic = {}
    def create_transaction(self, transaction, T_num):
        for block in transaction:
            print(f"\nT{T_num}, {block['variable']}")
            operation_name = block['operations'][0]
            lock_class = self.locks.get(block['variable']) # Fetch variable object from sharedExclusive class.
            if operation_name == 'read_item':
                if block['variable'] not in self.dic.keys():
                    self.dic[block['variable']] = [str(T_num)]
                    with lock_class.locking_item():
                        variable = lock_class.create_local_variable(block)
                        print(f"{block['variable']}:{variable}")
                        random_number = random.uniform(0.1,1.5)
                        print(f"~~ Sleep for {random_number:.2f} s")
                        sleep(random_number)
                    self.dic[block['variable']].remove(str(T_num))
                else:
                    if str(T_num) in self.dic[block['variable']]:
                        pass
                    else:
                        while len(self.dic[block['variable']]) > 0:
                            print("*",end="")
                        self.dic[block['variable']] = [str(T_num)]
                        with lock_class.locking_item():
                            variable = lock_class.create_local_variable(block)
                            print(f"{block['variable']}:{variable}")
                            random_number = random.uniform(0.1,1.5)
                            print(f"~~ Sleep for {random_number:.2f} s")
                            sleep(random_number)
                        self.dic[block['variable']].remove(str(T_num))
                print(self.dic)

                    
            elif operation_name == 'write_item':
                print('Im write item' + block['variable'])
                operation_task = block['operations'][1]
                if block['variable'] not in self.dic.keys():
                    self.dic[block['variable']] = [str(T_num)]
                else:
                    self.dic[block['variable']] += [str(T_num)]
                print(self.dic)
                # with lock_class.locking_item():
                #     variable = lock_class.create_local_variable(block)
                #     print(f"{block['variable']}:{variable}")
                #     operator, operand = operation_task.split()
                #     mapper = {
                #         '+' : _.add,
                #         '-' : _.sub,
                #         '*' : _.mul,
                #         '/' : _.truediv,
                #     }
                #     func = mapper.get(operator, None)
                #     if func:
                #         variable = func(variable, float(operand))
                #     random_number = random.uniform(0.1,1.5)
                #     print(f"~~ Sleep for {random_number:.2f} s")
                #     sleep(random_number)
                #     exec(f"lock_class.{block['variable']} = variable")

In [4]:
def create_and_run_threads(schedule, concurrency):
    for index, transaction in enumerate(schedule):
        exec(f"t{index} = Thread(target=concurrency.create_transaction, args=({transaction},{index+1}))")
    index += 1
    for i in range(index):
        exec(f"t{i}.start()")
    for i in range(index):
        exec(f"t{i}.join()")

def get_variables(schedule):
    vars = []
    for transaction in schedule:
        for block in transaction:
            vars.append(block['variable'])
    # Remove duplicates
    return list(set(vars))

def create_lock_objects(vars, BinaryLock):
    objects = {}
    for var in vars:
        ldic = locals()
        exec(f"objects[var] = BinaryLock()", ldic)
    return ldic['objects']

def print_variables(locks):
    print('\nAll used variables and values:')
    for var, obj in locks.items():
        print(var, "=", getattr(obj, var))
        
def main():
    transaction = [
        {
            'variable': "y",
            'operations': [
                'read_item', 
            ]
        },
        {
            'variable': "y",
            'operations': [
                'read_item', 
            ]
        },
        {
            'variable': "x",
            'operations': [
                'read_item', 
            ]
        },
        # {
        #     'variable': "x",
        #     'operations': [
        #         'write_item', 
        #         '+ 10'
        #     ]
        # },
    ]
    # for simplicity we assume all transactions are same.
    schedule = [transaction for _ in range(2)]
    print('hi')
    vars = get_variables(schedule)
    locks = create_lock_objects(vars, BinaryLock)
    concurrency = Concurrency(locks)
    print('hi')
    create_and_run_threads(schedule, concurrency)
    # print_variables(locks)

In [5]:
main()

hi
hi

T1, y

lock item called:
Acquire lock_item
y:0
~~ Sleep for 1.23 s

T2, y
*******************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

Exception in thread Thread-3:
Traceback (most recent call last):
  File "c:\Users\Lenovo\AppData\Local\Programs\Python\Python38\lib\threading.py", line 932, in _bootstrap_inner
    self.run()
  File "c:\Users\Lenovo\AppData\Local\Programs\Python\Python38\lib\threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "C:\Users\Lenovo\AppData\Local\Temp\ipykernel_2088\68691849.py", line 18, in create_transaction


****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

  File "c:\Users\Lenovo\AppData\Local\Programs\Python\Python38\lib\contextlib.py", line 120, in __exit__
    next(self.gen)
  File "C:\Users\Lenovo\AppData\Local\Temp\ipykernel_2088\4025211537.py", line 36, in locking_item
  File "C:\Users\Lenovo\AppData\Local\Temp\ipykernel_2088\4025211537.py", line 28, in lock_release


****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************

AttributeError: 'bool' object has no attribute 'release'


****************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************************